In [2]:
import pandas as pd
import os

In [3]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "for_sale_listings/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [5]:
# base cols RegionID,SizeRank,RegionName,RegionType,StateName

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        # ignore monthly data for now since it is redundant
        if "monthly" in filename:
            continue

        if "sfrcondo" in filename:
            cur_df["Home Type"] = "all homes"
        elif "sfr" in filename:
            cur_df["Home Type"] = "SFR"
        elif "condo" in filename:
            cur_df["Home Type"] = "condo/co-op only"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename

        if "_mlp_" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=(
                    "Median Listing Price"
                    if not smoothed
                    else "Median Listing Price (Smoothed)"
                ),
            )
            data_frames.append(cur_df)

        elif "_new_listings_" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=(
                    "New Listings" if not smoothed else "New Listings (Smoothed)"
                ),
            )
            data_frames.append(cur_df)

        elif "new_pending" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name="New Pending" if not smoothed else "New Pending (Smoothed)",
            )
            data_frames.append(cur_df)

matching_cols = [
    "RegionID",
    "Date",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]


def get_combined_df(data_frames):
    combined_df = None
    if len(data_frames) > 1:
        # iterate over dataframes and merge or concat
        combined_df = data_frames[0]
        for i in range(1, len(data_frames)):
            cur_df = data_frames[i]
            combined_df = pd.merge(
                combined_df,
                cur_df,
                on=[
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    "Date",
                ],
                suffixes=("", "_" + str(i)),
                how="outer",
            )
    elif len(data_frames) == 1:
        combined_df = data_frames[0]

    return combined_df


combined_df = get_combined_df(data_frames)


# iterate over rows of combined df and coalesce column values across columns that start with "Median Sale Price"
columns_to_coalesce = [
    "Median Listing Price",
    "Median Listing Price (Smoothed)",
    "New Listings",
    "New Listings (Smoothed)",
    "New Pending (Smoothed)",
    "New Pending",
]

for index, row in combined_df.iterrows():
    for col in combined_df.columns:
        for column_to_coalesce in columns_to_coalesce:
            if column_to_coalesce in col and "_" in col:
                if not pd.isna(row[col]):
                    combined_df.at[index, column_to_coalesce] = row[col]

# remove columns with underscores
combined_df = combined_df[[col for col in combined_df.columns if "_" not in col]]

combined_df

processing Metro_new_pending_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_month.csv
processing Metro_mlp_uc_sfr_sm_month.csv
processing Metro_new_pending_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfr_sm_week.csv
processing Metro_mlp_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_month.csv
processing Metro_mlp_uc_sfr_month.csv
processing Metro_new_listings_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_week.csv
processing Metro_new_listi

RegionID  SizeRank     RegionName RegionType StateName  Home Type  \
0         102001         0  United States    country       NaN        SFR   
1         102001         0  United States    country       NaN        SFR   
2         102001         0  United States    country       NaN        SFR   
3         102001         0  United States    country       NaN        SFR   
4         102001         0  United States    country       NaN        SFR   
...          ...       ...            ...        ...       ...        ...   
693656    845172       769   Winfield, KS        msa        KS  all homes   
693657    845172       769   Winfield, KS        msa        KS  all homes   
693658    845172       769   Winfield, KS        msa        KS  all homes   
693659    845172       769   Winfield, KS        msa        KS  all homes   
693660    845172       769   Winfield, KS        msa        KS  all homes   

              Date  New Pending (Smoothed)  Median Listing Price  \
0       2018-01-13                     NaN              259000.0   
1       2018-01-20                     NaN              259900.0   
2       2018-01-27                     NaN              259900.0   
3       2018-01-31                     NaN              254900.0   
4       2018-02-03                     NaN              260000.0   
...            ...                     ...                   ...   
693656  2023-12-16                     NaN              133938.0   
693657  2023-12-23                     NaN              126463.0   
693658  2023-12-30                     NaN              123225.0   
693659  2023-12-31                    24.0              136233.0   
693660  2024-01-06                     NaN              121488.0   

        Median Listing Price (Smoothed)  New Pending  New Listings  \
0                                   NaN          NaN           NaN   
1                                   NaN          NaN           NaN   
2                                   NaN          NaN           NaN   
3                                   NaN          NaN           NaN   
4                              259700.0          NaN           NaN   
...                                 ...          ...           ...   
693656                         133938.0          NaN           NaN   
693657                         126463.0          NaN           NaN   
693658                         123225.0          NaN           NaN   
693659                         136233.0         24.0          28.0   
693660                         121488.0          NaN           NaN   

        New Listings (Smoothed)  
0                           NaN  
1                           NaN  
2                           NaN  
3                           NaN  
4                           NaN  
...                         ...  
693656                      NaN  
693657                      NaN  
693658                      NaN  
693659                     28.0  
693660                      NaN  

[693661 rows x 13 columns]

In [6]:
final_df = combined_df
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df

Region ID  Size Rank         Region Region Type State  Home Type  \
0          102001          0  United States     country   NaN        SFR   
1          102001          0  United States     country   NaN        SFR   
2          102001          0  United States     country   NaN        SFR   
3          102001          0  United States     country   NaN        SFR   
4          102001          0  United States     country   NaN        SFR   
...           ...        ...            ...         ...   ...        ...   
693656     845172        769   Winfield, KS         msa    KS  all homes   
693657     845172        769   Winfield, KS         msa    KS  all homes   
693658     845172        769   Winfield, KS         msa    KS  all homes   
693659     845172        769   Winfield, KS         msa    KS  all homes   
693660     845172        769   Winfield, KS         msa    KS  all homes   

              Date  New Pending (Smoothed)  Median Listing Price  \
0       2018-01-13                     NaN              259000.0   
1       2018-01-20                     NaN              259900.0   
2       2018-01-27                     NaN              259900.0   
3       2018-01-31                     NaN              254900.0   
4       2018-02-03                     NaN              260000.0   
...            ...                     ...                   ...   
693656  2023-12-16                     NaN              133938.0   
693657  2023-12-23                     NaN              126463.0   
693658  2023-12-30                     NaN              123225.0   
693659  2023-12-31                    24.0              136233.0   
693660  2024-01-06                     NaN              121488.0   

        Median Listing Price (Smoothed)  New Pending  New Listings  \
0                                   NaN          NaN           NaN   
1                                   NaN          NaN           NaN   
2                                   NaN          NaN           NaN   
3                                   NaN          NaN           NaN   
4                              259700.0          NaN           NaN   
...                                 ...          ...           ...   
693656                         133938.0          NaN           NaN   
693657                         126463.0          NaN           NaN   
693658                         123225.0          NaN           NaN   
693659                         136233.0         24.0          28.0   
693660                         121488.0          NaN           NaN   

        New Listings (Smoothed)  
0                           NaN  
1                           NaN  
2                           NaN  
3                           NaN  
4                           NaN  
...                         ...  
693656                      NaN  
693657                      NaN  
693658                      NaN  
693659                     28.0  
693660                      NaN  

[693661 rows x 13 columns]

In [7]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)